# Import Libraries

In [155]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

# Standard plotly imports
import plotly.plotly as py
from plotly import tools
import plotly.graph_objs as go
from plotly.offline import iplot, init_notebook_mode

# Using plotly + cufflinks in offline mode
import cufflinks as cf
cf.go_offline(connected=True)
init_notebook_mode(connected=True)

# Load Dataset

In [156]:
df=pd.read_csv("C:/DataScienceProjects/20190703 Client subscriptions/2. Prepared Data/appdata10.csv")

In [159]:
df.head()

user               first_open  dayofweek       hour  age  \
0  235136  2012-12-27 02:14:51.273          3   02:00:00   23   
1  333588  2012-12-02 01:16:00.905          6   01:00:00   24   
2  254414  2013-03-19 19:19:09.157          1   19:00:00   23   
3  234192  2013-07-05 16:08:46.354          4   16:00:00   28   
4   51549  2013-02-26 18:50:48.661          1   18:00:00   31   

                                         screen_list  numscreens  minigame  \
0  idscreen,joinscreen,Cycle,product_review,ScanP...          15         0   
1  joinscreen,product_review,product_review2,Scan...          13         0   
2                                  Splash,Cycle,Loan           3         0   
3  product_review,Home,product_review,Loan3,Finan...          40         0   
4  idscreen,joinscreen,Cycle,Credit3Container,Sca...          32         0   

   used_premium_feature  enrolled            enrolled_date  liked  
0                     0         0                      NaN      0  
1                     0         0                      NaN      0  
2                     1         0                      NaN      1  
3                     0         1  2013-07-05 16:11:49.513      0  
4                     0         1  2013-02-26 18:56:37.841      1

In [160]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50000 entries, 0 to 49999
Data columns (total 12 columns):
user                    50000 non-null int64
first_open              50000 non-null object
dayofweek               50000 non-null int64
hour                    50000 non-null object
age                     50000 non-null int64
screen_list             50000 non-null object
numscreens              50000 non-null int64
minigame                50000 non-null int64
used_premium_feature    50000 non-null int64
enrolled                50000 non-null int64
enrolled_date           31074 non-null object
liked                   50000 non-null int64
dtypes: int64(8), object(4)
memory usage: 4.6+ MB


In [161]:
df.describe()

user     dayofweek          age    numscreens      minigame  \
count   50000.000000  50000.000000  50000.00000  50000.000000  50000.000000   
mean   186889.729900      3.029860     31.72436     21.095900      0.107820   
std    107768.520361      2.031997     10.80331     15.728812      0.310156   
min        13.000000      0.000000     16.00000      1.000000      0.000000   
25%     93526.750000      1.000000     24.00000     10.000000      0.000000   
50%    187193.500000      3.000000     29.00000     18.000000      0.000000   
75%    279984.250000      5.000000     37.00000     28.000000      0.000000   
max    373662.000000      6.000000    101.00000    325.000000      1.000000   

       used_premium_feature      enrolled         liked  
count          50000.000000  50000.000000  50000.000000  
mean               0.172020      0.621480      0.165000  
std                0.377402      0.485023      0.371184  
min                0.000000      0.000000      0.000000  
25%                0.000000      0.000000      0.000000  
50%                0.000000      1.000000      0.000000  
75%                0.000000      1.000000      0.000000  
max                1.000000      1.000000      1.000000

In [162]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50000 entries, 0 to 49999
Data columns (total 12 columns):
user                    50000 non-null int64
first_open              50000 non-null object
dayofweek               50000 non-null int64
hour                    50000 non-null object
age                     50000 non-null int64
screen_list             50000 non-null object
numscreens              50000 non-null int64
minigame                50000 non-null int64
used_premium_feature    50000 non-null int64
enrolled                50000 non-null int64
enrolled_date           31074 non-null object
liked                   50000 non-null int64
dtypes: int64(8), object(4)
memory usage: 4.6+ MB


# Data Cleaning

In [163]:
#converting hour to numeric
df['hour']=df["hour"].str.slice(1,3).astype(int)


# PLotting

In [164]:
# Histograms
df2=df.copy().drop(columns=['user','screen_list','enrolled_date','first_open','enrolled'])
df2.iplot(kind='histogram', subplots=True, shape=(3, 3),title='Distributions of numerical variables')

In [165]:
#Correlation with response
df2.corrwith(df['enrolled']).iplot(kind='bar',title='Correlation of numerical variables with outcome')

In [166]:
#Correlation Matrix
import plotly.figure_factory as ff
corrs = df2.corr()
figure = ff.create_annotated_heatmap(
    z=corrs.values,
    x=list(corrs.columns),
    y=list(corrs.index),
    annotation_text=corrs.round(2).values,
    showscale=True)
iplot(figure)

# Feature engineering

In [167]:
df.columns

Index(['user', 'first_open', 'dayofweek', 'hour', 'age', 'screen_list',
       'numscreens', 'minigame', 'used_premium_feature', 'enrolled',
       'enrolled_date', 'liked'],
      dtype='object')

In [168]:
#Convert to datetime 
datecolumns=['first_open','enrolled_date']
df[datecolumns]=df[datecolumns].applymap(lambda x : pd.to_datetime(x, errors='coerce'))


In [169]:
# Compute the diffrence between first_connection and enrolled date in hours
df['difference']=(df['enrolled_date']-df['first_open']).astype('timedelta64[h]')

In [170]:
# Plotting distribution of time difference beween first connection and enrolled date
df['difference'].dropna().iplot(kind='histogram',bins=(0,100,10))

Histogram above indicates us that most of the people are being enrolled within the first 50hours. It is an important information to fine tune our model and the response variable.
As the majority of the people being enrolled are being enrolled at a very early stage, we will limit people enrolled to the ones that have been enrolled within the first 48 hours (2 days).
Thus we could test the accuracy of our model within a 48 hours timeframe.

In [171]:
# creation of the second dataframe to be used with Tableau
df_tableau=df.copy()
# Reduce response variable to people entolled within 48 hours after first opening the app
df.loc[df.difference > 48, 'enrolled'] = 0

In [172]:
#Drop column that will not be used anymore
df=df.drop(columns =['difference','enrolled_date','first_open'])

# Formatting the screen list field

In [173]:
#Load the dataset referring to the opt screens
top_screens = pd.read_csv("C:/DataScienceProjects/20190703 Client subscriptions/2. Prepared Data/top_screens.csv").top_screens.values

In [174]:
# Adding a coma at the end for counting purpose (one , per screen)
df['screen_list']=df['screen_list'].astype(str) + ','
df_tableau['screen_list']=df_tableau['screen_list'].astype(str) + ','

In [175]:
for sc in top_screens:
    #Create a column for each popular screens and fill it with 1 or 0 if screen has been seen by user.
    df[sc] = df.screen_list.str.contains(sc).astype(int)
    df_tableau[sc] = df_tableau.screen_list.str.contains(sc).astype(int)
    #Take out the screens from the user's screen list
    df['screen_list'] = df.screen_list.str.replace(sc+",","")
    df_tableau['screen_list'] = df_tableau.screen_list.str.replace(sc+",","")

In [176]:
#Counting remaining screens (excluded from top_screen list) in an "Other" column
df['Other'] = df.screen_list.str.count(",")
df_tableau['Other'] = df_tableau.screen_list.str.count(",")

In [177]:
#Removing screen_list column
df = df.drop(columns=["screen_list"])
df_tableau = df_tableau.drop(columns=["screen_list"])

# Funnels

Screens usually belong to funnels like for example the Savings funnel. Screens within a funnel are often correlated and we want to remove this correlation. Hence, we will group screens according to the funnel they belongto.

In [178]:
# Creation of the Saving funnel
savings_screens = ["Saving1",
                   "Saving2",
                   "Saving2Amount",
                   "Saving4",
                   "Saving5",
                   "Saving6",
                   "Saving7",
                   "Saving8",
                   "Saving9",
                   "Saving10"
                  ]

In [179]:
#Counting number of screens from Savings funnel in one column
df["SavingsCount"]=df[savings_screens].sum(axis=1)
df_tableau["SavingsCount"]=df_tableau[savings_screens].sum(axis=1)
#Removing columns from the savings funnel
df=df.drop(columns=savings_screens)
df_tableau=df_tableau.drop(columns=savings_screens)

In [180]:
# Creation of the Credit Monitoring funnel
cm_screens = ["Credit1",
              "Credit2",
              "Credit3",
              "Credit3Container",
              "Credit3Dashboard"
             ]

In [181]:
#Counting number of screens from cm_screens funnel in one column
df["CMcount"] = df[cm_screens].sum(axis=1)
df_tableau["CMcount"] = df_tableau[cm_screens].sum(axis=1)
#Removing columns from the savings funnel
df = df.drop(columns=cm_screens)
df_tableau = df_tableau.drop(columns=cm_screens)

In [182]:
# Creation of the Credit Card funnel
cc_screens=["CC1",
          "CC1Category",
          "CC3"
         ]

In [183]:
#Counting number of screens from cm_screens funnel in one column
df["CCCount"] = df[cc_screens].sum(axis=1)
df_tableau["CCCount"] = df_tableau[cc_screens].sum(axis=1)
#Removing columns from the savings funnel
df=df.drop(columns=cc_screens)
df_tableau=df_tableau.drop(columns=cc_screens)

In [184]:
# Creation of the Loan funnel
loan_screens = ["Loan",
               "Loan2",
               "Loan3",
               "Loan4"]

In [185]:
#Counting number of screens from cm_screens funnel in one column
df["LoansCount"] = df[loan_screens].sum(axis=1)
df_tableau["LoansCount"] = df_tableau[loan_screens].sum(axis=1)
#Removing columns from the savings funnel
df=df.drop(columns=loan_screens)
df_tableau=df_tableau.drop(columns=loan_screens)

In [186]:
df.describe()

user     dayofweek          hour          age    numscreens  \
count   50000.000000  50000.000000  50000.000000  50000.00000  50000.000000   
mean   186889.729900      3.029860     12.557220     31.72436     21.095900   
std    107768.520361      2.031997      7.438072     10.80331     15.728812   
min        13.000000      0.000000      0.000000     16.00000      1.000000   
25%     93526.750000      1.000000      5.000000     24.00000     10.000000   
50%    187193.500000      3.000000     14.000000     29.00000     18.000000   
75%    279984.250000      5.000000     19.000000     37.00000     28.000000   
max    373662.000000      6.000000     23.000000    101.00000    325.000000   

           minigame  used_premium_feature      enrolled         liked  \
count  50000.000000          50000.000000  50000.000000  50000.000000   
mean       0.107820              0.172020      0.497000      0.165000   
std        0.310156              0.377402      0.499996      0.371184   
min        0.000000              0.000000      0.000000      0.000000   
25%        0.000000              0.000000      0.000000      0.000000   
50%        0.000000              0.000000      0.000000      0.000000   
75%        0.000000              0.000000      1.000000      0.000000   
max        1.000000              1.000000      1.000000      1.000000   

           location      ...       SecurityModal   ResendToken  \
count  50000.000000      ...        50000.000000  50000.000000   
mean       0.517760      ...            0.014220      0.013340   
std        0.499689      ...            0.118398      0.114727   
min        0.000000      ...            0.000000      0.000000   
25%        0.000000      ...            0.000000      0.000000   
50%        1.000000      ...            0.000000      0.000000   
75%        1.000000      ...            0.000000      0.000000   
max        1.000000      ...            1.000000      1.000000   

       TransactionList  NetworkFailure    ListPicker         Other  \
count     50000.000000    50000.000000  50000.000000  50000.000000   
mean          0.013400        0.008200      0.007580      6.214260   
std           0.114981        0.090183      0.086733      3.672561   
min           0.000000        0.000000      0.000000      0.000000   
25%           0.000000        0.000000      0.000000      3.000000   
50%           0.000000        0.000000      0.000000      6.000000   
75%           0.000000        0.000000      0.000000      8.000000   
max           1.000000        1.000000      1.000000     35.000000   

       SavingsCount      CMcount       CCCount    LoansCount  
count  50000.000000  50000.00000  50000.000000  50000.000000  
mean       0.365020      0.92776      0.176860      0.788400  
std        1.405511      1.21751      0.612787      0.677462  
min        0.000000      0.00000      0.000000      0.000000  
25%        0.000000      0.00000      0.000000      0.000000  
50%        0.000000      0.00000      0.000000      1.000000  
75%        0.000000      1.00000      0.000000      1.000000  
max       10.000000      5.00000      3.000000      3.000000  

[8 rows x 50 columns]

In [188]:
#Recording datasets as csv file
df_tableau.to_csv("C:/DataScienceProjects/20190703 Client subscriptions/3. Uploaded Data/subsappdata_tableau.csv",index=False)
df.to_csv("C:/DataScienceProjects/20190703 Client subscriptions/3. Uploaded Data/subsappdata.csv",index=False)
